<h1>Table of Contents<span class="tocSkip"></span></h1>
<div class="toc"><ul class="toc-item"><li><span><a href="#Architecture-of-CNN" data-toc-modified-id="Architecture-of-CNN-1"><span class="toc-item-num">1&nbsp;&nbsp;</span>Architecture of CNN</a></span></li><li><span><a href="#CNN-Pipeline" data-toc-modified-id="CNN-Pipeline-2"><span class="toc-item-num">2&nbsp;&nbsp;</span>CNN Pipeline</a></span><ul class="toc-item"><li><span><a href="#Imports" data-toc-modified-id="Imports-2.1"><span class="toc-item-num">2.1&nbsp;&nbsp;</span>Imports</a></span></li><li><span><a href="#Import-Test-and-Train-Data" data-toc-modified-id="Import-Test-and-Train-Data-2.2"><span class="toc-item-num">2.2&nbsp;&nbsp;</span>Import Test and Train Data</a></span></li><li><span><a href="#Normalize-data" data-toc-modified-id="Normalize-data-2.3"><span class="toc-item-num">2.3&nbsp;&nbsp;</span>Normalize data</a></span></li><li><span><a href="#Create-Feature-Column" data-toc-modified-id="Create-Feature-Column-2.4"><span class="toc-item-num">2.4&nbsp;&nbsp;</span>Create Feature Column</a></span></li><li><span><a href="#Create-Model" data-toc-modified-id="Create-Model-2.5"><span class="toc-item-num">2.5&nbsp;&nbsp;</span>Create Model</a></span><ul class="toc-item"><li><span><a href="#Input-Layer" data-toc-modified-id="Input-Layer-2.5.1"><span class="toc-item-num">2.5.1&nbsp;&nbsp;</span>Input Layer</a></span></li><li><span><a href="#Convolution-Layer-and-Pooling-Layer" data-toc-modified-id="Convolution-Layer-and-Pooling-Layer-2.5.2"><span class="toc-item-num">2.5.2&nbsp;&nbsp;</span>Convolution Layer and Pooling Layer</a></span><ul class="toc-item"><li><span><a href="#Convolution-Layer" data-toc-modified-id="Convolution-Layer-2.5.2.1"><span class="toc-item-num">2.5.2.1&nbsp;&nbsp;</span>Convolution Layer</a></span></li><li><span><a href="#Pooling-Layer" data-toc-modified-id="Pooling-Layer-2.5.2.2"><span class="toc-item-num">2.5.2.2&nbsp;&nbsp;</span>Pooling Layer</a></span></li></ul></li><li><span><a href="#2nd-Hidden-Layer" data-toc-modified-id="2nd-Hidden-Layer-2.5.3"><span class="toc-item-num">2.5.3&nbsp;&nbsp;</span>2nd Hidden Layer</a></span></li><li><span><a href="#Dense-Layer" data-toc-modified-id="Dense-Layer-2.5.4"><span class="toc-item-num">2.5.4&nbsp;&nbsp;</span>Dense Layer</a></span></li><li><span><a href="#Logit-Layer" data-toc-modified-id="Logit-Layer-2.5.5"><span class="toc-item-num">2.5.5&nbsp;&nbsp;</span>Logit Layer</a></span></li><li><span><a href="#Calculate-Loss" data-toc-modified-id="Calculate-Loss-2.5.6"><span class="toc-item-num">2.5.6&nbsp;&nbsp;</span>Calculate Loss</a></span></li><li><span><a href="#Optimize-the-model" data-toc-modified-id="Optimize-the-model-2.5.7"><span class="toc-item-num">2.5.7&nbsp;&nbsp;</span>Optimize the model</a></span></li><li><span><a href="#Display-the-Metrics" data-toc-modified-id="Display-the-Metrics-2.5.8"><span class="toc-item-num">2.5.8&nbsp;&nbsp;</span>Display the Metrics</a></span></li></ul></li><li><span><a href="#Initialize-the-Model" data-toc-modified-id="Initialize-the-Model-2.6"><span class="toc-item-num">2.6&nbsp;&nbsp;</span>Initialize the Model</a></span></li><li><span><a href="#Train-the-model" data-toc-modified-id="Train-the-model-2.7"><span class="toc-item-num">2.7&nbsp;&nbsp;</span>Train the model</a></span></li><li><span><a href="#Evaluate-the-model" data-toc-modified-id="Evaluate-the-model-2.8"><span class="toc-item-num">2.8&nbsp;&nbsp;</span>Evaluate the model</a></span></li></ul></li></ul></div>

# Architecture of CNN

<img src='artifacts/cnn1.png' />

We will be using the MNIST dataset.<br>
Basic example of a dataset is:
<img src='artifacts/cnn2.png'/>

# CNN Pipeline

## Imports

In [6]:
import numpy as np
import tensorflow.compat.v1 as tf
from sklearn.datasets import fetch_openml
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import MinMaxScaler
tf.disable_eager_execution()

## Import Test and Train Data

In [4]:
mnist = fetch_openml('mnist_784', data_home='data/mnist')
print(mnist.data.shape)
print(mnist.target.shape)

(70000, 784)
(70000,)


In [15]:
# Model Dir
model_dir = 'logs/12_cnn_mnist'

In [5]:
X_train, X_test, Y_train, Y_test = train_test_split(mnist.data, mnist.target, test_size = 0.2, random_state = 42)
Y_test = Y_test.astype(int)
Y_train = Y_train.astype(int)
print(X_train.shape)
print(Y_train.shape)
print(X_test.shape)
print(Y_test.shape)

(56000, 784)
(56000,)
(14000, 784)
(14000,)


## Normalize data

In [7]:
scaler = MinMaxScaler()
X_train_scaled = scaler.fit_transform(X_train.astype(np.float64))
X_test_scaled = scaler.fit_transform(X_test.astype(np.float64))
print(X_test_scaled.shape)
print(X_train_scaled.shape)

(14000, 784)
(56000, 784)


## Create Feature Column

In [10]:
feature_columns = [tf.feature_column.numeric_column('X', shape = X_train_scaled.shape[1])]

## Create Model

- Convolutional Layer: Applies 14 5x5 filters (extracting 5x5-pixel subregions), with ReLU activation function
- Pooling Layer: Performs max pooling with a 2x2 filter and stride of 2 (which specifies that pooled regions do not overlap)
- Convolutional Layer: Applies 36 5x5 filters, with ReLU activation function
- Pooling Layer #2: Again, performs max pooling with a 2x2 filter and stride of 2
1,764 neurons, with dropout regularization rate of 0.4 (probability of 0.4 that any given element will be dropped during training)
- Dense Layer (Logits Layer): 10 neurons, one for each digit target class (0–9).

### Input Layer

We need to define a tensor with the shape of the data. For that, you can use the module tf.reshape.<br>
A picture has a height, a width, and a channel. The MNIST dataset is a monochronic picture with a 28x28 size.<br>
We set the batch size to -1 in the shape argument so that it takes the shape of the features["x"]. The advantage is to make the batch size hyperparameters to tune.<br>
Eg: <i>If the batch size is set to 7, then the tensor will feed 5,488 values (28*28*7).<i>

<code>def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(tensor = features['X'], shape = [-1, 28, 28, 1])
</code>

### Convolution Layer and Pooling Layer

#### Convolution Layer

The first convolutional layer has 14 filters with a kernel size of 5x5 with the same padding.<br>
Thus the output size will be [batch_size, 28, 28, 14].

<code>conv_layer_1 = tf.layers.conv2d(
    inputs = input_layer,
    filters = 14,
    kernel_size = [5,5], #filter size
    padding = 'same',
    activation = tf.nn.relu)<code>

#### Pooling Layer

we will use the module max_pooling2d with a size of 2x2 and stride of 2 and use the previous layer as input. The output size will be [batch_size, 14, 14, 14].

<code>max_pool_layer_1 = tf.layers.max_pooling2d(
    inputs = conv_layer_1,
    pool_size = [2, 2],
    strides = 2)</code>

### 2nd Hidden Layer

The second convolutional layer has 32 filters, with an output size of [batch_size, 14, 14, 36]. The pooling layer has the same size as before and the output shape is [batch_size, 7, 7, 36].

<code>conv_layer_2 = tf.layers.conv2d(
    inputs = max_pool_layer_1,
    filters = 36,
    kerne_size = [5, 5],
    activation = tf.nn.relu)

max_pool_layer_2 = tf.layers.max_pooling2d(
    inputs = conv_layer_2,
    pool_size = [2, 2],
    strides = 2)</code>

### Dense Layer

The ouput of the above pooling layer will be 7*7*36 = 1764. Thus the dense layer will have an input of 1764 neurons. We will also use a Dropout Regularization with rate = 0.3, meaning 30 percents of the weights will be set to 0.<br>
Dropout should only occur in training phase and not in evaluation phase. Thus we will put a check here.

<code>max_pool_2_flat = tf.reshape(max_pool_2, [-1, 7* 7* 36])
dense = tf.layers.dense(inputs = max_pool_2_flat, units = 7* 7* 36, activation = tf.nn.relu)
dropout = tf.layers.dropout(inputs = dense, training = mode == tf.estimator.ModeKeys.TRAIN)</code>

### Logit Layer

There are 10 classes to identify, thus the output will be [bathc_size, 10]. Here we will also apply the Softmax Function. <br>
We have to return a prediction object if the mode is set to prediction.

<code>logits = tf.layers.dense(inputs = dropout, units = 10)
predictions = {
    'classes': tf.argmax(inputs = logits, axis = 1),
    'probabilities': tf.nn.softmax(logits, name = 'softmax_tensor')
    }
if mode == tf.estimator.ModeKeys.PREDICT:
    return tf.estimator.EstimatorSpec(mode = mode, predictions = predictions)</code>

### Calculate Loss

This step is used for both TRAIN and EVAL modes.<br>

<code>loss = tf.losses.sparse_softmax_cross_entropy(labels = labels, logits = logits)</code>

### Optimize the model

Here we will use the Gradient Descent Optimizer to optimize the Convolution Neural Network. The learning rate will be 0.001.

<code>optimizer = tf.train.GradientDescentOptimizer(learning_rate = 0.001)
train_op = optimizer.minimize(loss =loss, global_step = tf.train.get_global_step())</code>

### Display the Metrics

We would like to display the performance metric during the EVAL mode.<br>
<code>eval_metric_ops = {
    'accuracy' : tf.metrics.accuracy(labels = labels, prediction = predictions['classes'])
}
return tf.estimator.EstimatorSpec(mode = mode, loss = loss, eval_metric_ops = eval_metric_ops)</code>

In [50]:
#code
def cnn_model_fn(features, labels, mode):
    input_layer = tf.reshape(tensor = features['X'], shape = [-1, 28, 28, 1])
    
    # conv 1
    conv_layer_1 = tf.layers.conv2d(
        inputs = input_layer,
        filters = 32,
        kernel_size = [5,5], #filter size
        padding = 'same',
        activation = tf.nn.relu)
    
    #pool1
    max_pool_layer_1 = tf.layers.max_pooling2d(
        inputs = conv_layer_1,
        pool_size = [2, 2],
        strides = 2)
    
    #conv2
    conv_layer_2 = tf.layers.conv2d(
        inputs = max_pool_layer_1,
        filters = 36,
        kernel_size = [5, 5],
        padding = 'same',
        activation = tf.nn.relu)
    
    #pool2
    max_pool_layer_2 = tf.layers.max_pooling2d(
        inputs = conv_layer_2,
        pool_size = [2, 2],
        strides = 2)
    
    #dense
    max_pool_2_flat = tf.reshape(max_pool_layer_2, [-1, 7* 7* 36])
    dense = tf.layers.dense(inputs = max_pool_2_flat, units = 7* 7* 36, activation = tf.nn.relu)
    dropout = tf.layers.dropout(inputs = dense, training = mode == tf.estimator.ModeKeys.TRAIN)
    
    #logits
    logits = tf.layers.dense(inputs = dropout, units = 10)
    predictions = {
        'classes': tf.argmax(input = logits, axis = 1),
        'probabilities': tf.nn.softmax(logits, name = 'softmax_tensor')
    }
    if mode == tf.estimator.ModeKeys.PREDICT:
        return tf.estimator.EstimatorSpec(mode = mode, predictions = predictions)
    
    #loss function
    loss = tf.losses.sparse_softmax_cross_entropy(labels = labels, logits = logits)
    
    #optimize the loss function for TRAIN mode
    if mode == tf.estimator.ModeKeys.TRAIN:
        optimizer = tf.train.GradientDescentOptimizer(learning_rate = 0.001)
        train_op = optimizer.minimize(loss =loss, global_step = tf.train.get_global_step())
        return tf.estimator.EstimatorSpec(mode = mode, loss = loss, train_op = train_op)
    
    #display loss and evaluation metric for EVAL mode
    eval_metric_ops = {
        'accuracy' : tf.metrics.accuracy(labels = labels, predictions = predictions['classes'])
    }
    return tf.estimator.EstimatorSpec(mode = mode, loss = loss, eval_metric_ops = eval_metric_ops)

## Initialize the Model

In [51]:
mnist_estimator = tf.estimator.Estimator(
    model_fn = cnn_model_fn,
    model_dir=model_dir)

INFO:tensorflow:Using default config.
INFO:tensorflow:Using config: {'_model_dir': 'logs/12_cnn_mnist', '_tf_random_seed': None, '_save_summary_steps': 100, '_save_checkpoints_steps': None, '_save_checkpoints_secs': 600, '_session_config': allow_soft_placement: true
graph_options {
  rewrite_options {
    meta_optimizer_iterations: ONE
  }
}
, '_keep_checkpoint_max': 5, '_keep_checkpoint_every_n_hours': 10000, '_log_step_count_steps': 100, '_train_distribute': None, '_device_fn': None, '_protocol': None, '_eval_distribute': None, '_experimental_distribute': None, '_experimental_max_worker_delay_secs': None, '_session_creation_timeout_secs': 7200, '_service': None, '_cluster_spec': <tensorflow.python.training.server_lib.ClusterSpec object at 0x7f43fb622890>, '_task_type': 'worker', '_task_id': 0, '_global_id_in_cluster': 0, '_master': '', '_evaluation_master': '', '_is_chief': True, '_num_ps_replicas': 0, '_num_worker_replicas': 1}


## Train the model

A CNN takes many times to train, therefore, you create a Logging hook to store the values of the softmax layers every 50 iterations.

In [52]:
# Set up logging for predictions
tensors_to_log = {"probabilities": "softmax_tensor"}
logging_hook = tf.train.LoggingTensorHook(tensors=tensors_to_log, every_n_iter=50)

In [53]:
!rm -rf logs/12_cnn_mnist
train_input_fn = tf.estimator.inputs.numpy_input_fn(x = {'X' : X_train_scaled},
                                                   y = Y_train,
                                                   batch_size = 100,
                                                   num_epochs = None,
                                                   shuffle = True)
mnist_estimator.train(input_fn = train_input_fn,
                     steps = 16000,
                     hooks = [logging_hook])

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Create CheckpointSaverHook.
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
Instructions for updating:
To construct input pipelines, use the `tf.data` module.
INFO:tensorflow:Saving checkpoints for 0 into logs/12_cnn_mnist/model.ckpt.
INFO:tensorflow:probabilities = [[0.10535067 0.10264228 0.09598516 0.10118145 0.09566601 0.10196263
  0.09962101 0.08342257 0.09949188 0.11467634]
 [0.09573594 0.1007115  0.10108069 0.09474646 0.08966769 0.10401931
  0.08751864 0.09802513 0.11074411 0.11775054]
 [0.09507348 0.10335277 0.10093652 0.09088116 0.10236475 0.10426108
  0.08999097 0.08890541 0.11544835 0.10878551]
 [0.09949253 0.1051121  0.09936464 0.10455646 0.08973786 0.10738771
  0.09028748 0.09305725 0.10226908 0.1087349 ]
 [0.10607865 0.101239   0.09471832 0.10237238 0.10524291 0.09279439
  0.0858746  0.09344255 0.11334382 0.1048933

INFO:tensorflow:loss = 2.3181509971618652, step = 0
INFO:tensorflow:probabilities = [[0.0960315  0.10020894 0.09584394 0.09791186 0.09960724 0.08955671
  0.09223702 0.11066882 0.10428092 0.11365304]
 [0.10346341 0.0934414  0.09737781 0.10539943 0.09763212 0.09666056
  0.09409881 0.09284912 0.1025155  0.11656184]
 [0.08547469 0.10723326 0.11046409 0.10061833 0.095703   0.10351188
  0.0906489  0.09049779 0.10486252 0.11098554]
 [0.09674305 0.10264497 0.10920772 0.09998947 0.08587435 0.10223752
  0.09323693 0.08828046 0.11030824 0.11147729]
 [0.10220901 0.09042136 0.09506217 0.10272129 0.09138261 0.10157157
  0.09864686 0.09837917 0.10932179 0.11028418]
 [0.10197255 0.10352533 0.10649835 0.09577838 0.10010305 0.10442366
  0.09109235 0.09730318 0.09954465 0.09975849]
 [0.09643564 0.0971463  0.11199583 0.09658087 0.09657627 0.09948087
  0.091872   0.09800869 0.10267916 0.10922437]
 [0.09732148 0.09935672 0.10400109 0.09610823 0.10156129 0.10207758
  0.09781296 0.09500211 0.10212205 0.104636

INFO:tensorflow:global_step/sec: 2.52871
INFO:tensorflow:probabilities = [[0.09755898 0.10270015 0.09890774 0.10474379 0.0906992  0.08806219
  0.08723478 0.09117859 0.11585384 0.12306074]
 [0.09825002 0.09957721 0.10408107 0.09483621 0.10080763 0.09800772
  0.08840235 0.09731494 0.10760073 0.11112211]
 [0.10137421 0.0965542  0.10335509 0.10719556 0.09310747 0.10069925
  0.09798614 0.08287788 0.10181891 0.1150313 ]
 [0.10610341 0.10754017 0.10277132 0.10177589 0.09771403 0.09347228
  0.08470902 0.09540443 0.09476994 0.11573951]
 [0.09375052 0.11063902 0.11349417 0.10129815 0.09865247 0.10458722
  0.08743965 0.09250184 0.09086351 0.10677346]
 [0.09015434 0.10030736 0.09825103 0.10294287 0.09518179 0.10634699
  0.09334451 0.10290625 0.11346356 0.0971013 ]
 [0.10016328 0.10138904 0.09821538 0.10086983 0.10351386 0.09960621
  0.09145548 0.09144119 0.10558226 0.10776346]
 [0.09807852 0.10512476 0.11039321 0.0960929  0.09789713 0.09774713
  0.0904333  0.09494593 0.1057789  0.10350822]
 [0.109

INFO:tensorflow:loss = 2.3090691566467285, step = 100 (39.557 sec)
INFO:tensorflow:probabilities = [[0.1070224  0.10954453 0.10171814 0.09840009 0.09294324 0.09618639
  0.09714182 0.09720148 0.105909   0.09393292]
 [0.10409081 0.10628054 0.09790729 0.10032115 0.09839956 0.08990961
  0.09052497 0.08516777 0.11783417 0.10956414]
 [0.10485718 0.10273044 0.10788135 0.10616989 0.09258735 0.0935929
  0.08418228 0.09190184 0.10547091 0.11062585]
 [0.10706113 0.10523573 0.07988442 0.1003269  0.09949866 0.09219394
  0.09538417 0.10318329 0.10580242 0.11142935]
 [0.10487136 0.11080883 0.10754855 0.09942216 0.09798223 0.1024521
  0.08415729 0.09465669 0.09264926 0.10545153]
 [0.09519938 0.09601755 0.10352306 0.09863728 0.09523864 0.08991469
  0.09310677 0.10186993 0.1133658  0.1131269 ]
 [0.10640768 0.09559166 0.10076115 0.08964686 0.09726385 0.09344235
  0.09215467 0.09874374 0.10218118 0.12380686]
 [0.10221262 0.09698322 0.10450909 0.10008408 0.10457425 0.11094022
  0.08673734 0.08831578 0.1022

INFO:tensorflow:global_step/sec: 2.58183
INFO:tensorflow:probabilities = [[0.09790063 0.10294006 0.09555898 0.10286534 0.11153304 0.09682862
  0.08990066 0.09689121 0.10686683 0.09871463]
 [0.11021613 0.0907397  0.10120078 0.10230003 0.0925672  0.09421437
  0.09844735 0.09028581 0.10816572 0.11186291]
 [0.10041232 0.1044112  0.10619017 0.09680545 0.09439814 0.09458965
  0.09543745 0.09586958 0.10101429 0.11087175]
 [0.0965398  0.10760996 0.10961465 0.1047474  0.09872011 0.09486899
  0.09652281 0.08997606 0.09731153 0.1040887 ]
 [0.09582033 0.10080421 0.09385136 0.10435343 0.09319788 0.09645616
  0.09721538 0.10702888 0.10422873 0.10704364]
 [0.10182784 0.09382652 0.09679875 0.09908655 0.1038114  0.09350615
  0.08847906 0.11051393 0.10176101 0.1103888 ]
 [0.09307625 0.10349807 0.11145087 0.09683233 0.08496052 0.09627102
  0.09678777 0.09877987 0.10183813 0.11650517]
 [0.10052959 0.09771157 0.10496987 0.1007098  0.09873714 0.10037309
  0.09733241 0.08668145 0.10729953 0.10565556]
 [0.108

...

INFO:tensorflow:global_step/sec: 3.60527
INFO:tensorflow:probabilities = [[0.00000035 0.00000735 0.00000148 0.00010178 0.00000312 0.00000899
  0.         0.99876785 0.00000234 0.00110673]
 [0.00000001 0.0000041  0.00003158 0.99880908 0.         0.00045422
  0.00000001 0.00000015 0.00070029 0.00000056]
 [0.02936919 0.00000044 0.96869876 0.00004504 0.00000261 0.0000073
  0.00052133 0.00000175 0.00126018 0.0000934 ]
 [0.00005232 0.00000043 0.00000609 0.00000006 0.99777615 0.00011149
  0.00021813 0.00037482 0.00012614 0.00133437]
 [0.00019715 0.97994687 0.00053708 0.00036005 0.00012451 0.00026868
  0.00325535 0.0002134  0.01492235 0.00017457]
 [0.0000029  0.00000077 0.00026925 0.00000158 0.00006653 0.00019676
  0.99803991 0.00000003 0.00141981 0.00000247]
 [0.00011276 0.00439195 0.00518404 0.86153105 0.00000113 0.1282804
  0.00001819 0.00001745 0.00020897 0.00025407]
 [0.00000696 0.00000261 0.00030599 0.99438385 0.00000001 0.00510326
  0.00000001 0.00000257 0.00013963 0.00005513]
 [0.00114

INFO:tensorflow:loss = 0.08459684252738953, step = 15800 (27.738 sec)
INFO:tensorflow:probabilities = [[0.00123632 0.00033819 0.00223873 0.0000118  0.00046735 0.00215238
  0.98966388 0.00000055 0.0038497  0.00004111]
 [0.00038071 0.00003679 0.00651699 0.04179371 0.00001745 0.49704808
  0.00139529 0.0000021  0.45275903 0.00004986]
 [0.00000083 0.00006045 0.00030032 0.00025231 0.61720192 0.000712
  0.00010801 0.00028064 0.00374145 0.37734207]
 [0.00009405 0.00000113 0.00094137 0.00090007 0.0000013  0.01320712
  0.00010446 0.00000009 0.98461145 0.00013896]
 [0.00002347 0.09634975 0.84663962 0.03701652 0.00992107 0.00417629
  0.00323276 0.00047869 0.00165025 0.00051158]
 [0.00000974 0.00001516 0.00045537 0.00006164 0.0000039  0.00000412
  0.00000001 0.9982228  0.00009396 0.0011333 ]
 [0.00000022 0.00000238 0.0000049  0.00112236 0.04301475 0.00107149
  0.00000008 0.84921283 0.00000315 0.10556783]
 [0.00000006 0.00000317 0.00000058 0.00011955 0.01271563 0.00194292
  0.00000004 0.00076543 0.0

INFO:tensorflow:global_step/sec: 3.54277
INFO:tensorflow:probabilities = [[0.00006842 0.00000136 0.00000209 0.00000267 0.0000104  0.00002097
  0.00000016 0.99594363 0.00000443 0.00394588]
 [0.00000083 0.00025659 0.00009392 0.0004536  0.92045346 0.00007496
  0.00009226 0.00214493 0.0082891  0.06814036]
 [0.00000005 0.00000032 0.00000659 0.9999576  0.         0.00002823
  0.         0.00000005 0.0000071  0.00000006]
 [0.00000113 0.00002289 0.00034952 0.00017039 0.00000165 0.00000038
  0.         0.99915281 0.0000134  0.00028784]
 [0.00000084 0.00335896 0.00003502 0.00128413 0.96961893 0.00056175
  0.00008146 0.00009506 0.00333915 0.0216247 ]
 [0.00000015 0.00000021 0.00008886 0.00003582 0.00022855 0.00000007
  0.00000005 0.99910396 0.00008487 0.00045746]
 [0.00010655 0.00248716 0.05927036 0.00435259 0.00044977 0.01313577
  0.00000197 0.00620199 0.00329571 0.91069813]
 [0.99729384 0.00000001 0.00003313 0.00010632 0.00000001 0.00063603
  0.00000231 0.00000184 0.00162383 0.00030269]
 [0.000

INFO:tensorflow:loss = 0.10083369165658951, step = 15900 (28.241 sec)
INFO:tensorflow:probabilities = [[0.00025202 0.00003003 0.00018922 0.00007776 0.00002351 0.00095046
  0.00570611 0.00000008 0.99273047 0.00004033]
 [0.00007127 0.00000009 0.0001675  0.99975031 0.00000001 0.00000602
  0.         0.00000043 0.00000039 0.000004  ]
 [0.00000097 0.99819589 0.00006524 0.00108621 0.00001687 0.00001039
  0.0000067  0.00008192 0.00052546 0.00001035]
 [0.0000517  0.00000316 0.00001007 0.00000167 0.00081552 0.00053279
  0.99852913 0.0000001  0.00005494 0.00000091]
 [0.00000631 0.00002063 0.0000034  0.00260229 0.00637079 0.00093534
  0.00000037 0.00132934 0.00149697 0.98723456]
 [0.04105088 0.00000087 0.00463656 0.00015191 0.0000504  0.00106956
  0.00000011 0.93751008 0.00017328 0.01535637]
 [0.00005349 0.00001654 0.00044613 0.00001602 0.00002793 0.00482132
  0.00518416 0.00000559 0.98941354 0.00001528]
 [0.00027137 0.00000462 0.00024552 0.00051639 0.00007918 0.41371031
  0.0229686  0.00000151 0

INFO:tensorflow:Saving checkpoints for 16000 into logs/12_cnn_mnist/model.ckpt.
INFO:tensorflow:Loss for final step: 0.18636296689510345.


## Evaluate the model

In [54]:
eval_input_fn = tf.estimator.inputs.numpy_input_fn(x = {'X' : X_test_scaled},
                                                  y = Y_test,
                                                  num_epochs = 1,
                                                  shuffle = False)
eval_result = mnist_estimator.evaluate(input_fn = eval_input_fn)
print(eval_result)

INFO:tensorflow:Calling model_fn.
INFO:tensorflow:Done calling model_fn.
INFO:tensorflow:Starting evaluation at 2020-04-02T20:57:52Z
INFO:tensorflow:Graph was finalized.
INFO:tensorflow:Restoring parameters from logs/12_cnn_mnist/model.ckpt-16000
INFO:tensorflow:Running local_init_op.
INFO:tensorflow:Done running local_init_op.
INFO:tensorflow:Finished evaluation at 2020-04-02-20:58:01
INFO:tensorflow:Saving dict for global step 16000: accuracy = 0.95914286, global_step = 16000, loss = 0.13944052
INFO:tensorflow:Saving 'checkpoint_path' summary for global step 16000: logs/12_cnn_mnist/model.ckpt-16000
{'accuracy': 0.95914286, 'loss': 0.13944052, 'global_step': 16000}
